In [1]:
import asyncio
import ccxt.async_support as ccxt

- To get a list of all available methods with an exchange instance, you can simply do the following:

In [2]:
print(dir(ccxt.hitbtc()))

['__aenter__', '__aexit__', '__annotations__', '__class__', '__del__', '__delattr__', '__dict__', '__dir__', '__doc__', '__eq__', '__format__', '__ge__', '__getattribute__', '__getstate__', '__gt__', '__hash__', '__init__', '__init_subclass__', '__le__', '__lt__', '__module__', '__ne__', '__new__', '__reduce__', '__reduce_ex__', '__repr__', '__setattr__', '__sizeof__', '__str__', '__subclasshook__', '__weakref__', 'account', 'accountId', 'accounts', 'addMargin', 'add_margin', 'afterConstruct', 'after_construct', 'aggregate', 'aiohttpProxy', 'aiohttpTrustEnv', 'aiohttp_proxy', 'aiohttp_trust_env', 'alias', 'amountToPrecision', 'amount_to_precision', 'api', 'apiKey', 'arrayConcat', 'arraySlice', 'array_concat', 'array_slice', 'assignDefaultDepositWithdrawFees', 'assign_default_deposit_withdraw_fees', 'asyncioLoop', 'asyncio_loop', 'axolotl', 'balance', 'base16ToBinary', 'base16_to_binary', 'base58Alphabet', 'base58Decoder', 'base58Encoder', 'base58ToBinary', 'base58_alphabet', 'base58_de

- In async mode you have all the same properties and methods, but most methods are decorated with an async keyword. If you want to use async mode, you should link against the ccxt.async_support subpackage

In [ ]:
async def print_poloniex_dogebtc_ticker():
    poloniex = ccxt.poloniex()
    print(poloniex.fetch_ticker('DOGE/BTC'))
    await poloniex.close()

asyncio.run(print_poloniex_dogebtc_ticker())

## Passing Parameters to API Methods
- The set of all possible API endpoints differs from exchange to exchange. Most of methods accept a single associative array (or a Python dict) of key-value parameters. The params are passed as follows:

In [ ]:
ccxt.zaif().public_get_ticker_pair({'pair': 'btc_jpy'})

In [ ]:
zaif = ccxt.zaif()
zaif.fetch_markets()

In [ ]:
zaif.fetch_currencies()

In [ ]:
zaif.load_markets()

#### The means of pagination are often used with the following methods in particular:

- fetch_trades()
- fetch_ohlcv()
- fetch_orders()
- fetch_canceled_orders()
- fetch_closed_order()
- fetch_closed_orders()
- fetch_open_order()
- fetch_open_orders()
- fetch_my_trades()
- fetch_transactions()
- fetch_deposit()
- fetch_deposits()
- fetch_withdrawals()

#### We have three different ways of paginating:

- dynamic/time-based: uses the until and since parameters to paginate through dynamic results like (trades, orders, transactions, etc). Since we don't know a priori how many entries are available to be fetched, it will perform one request at a time until we reach the end of the data or the maximum amount of pagination calls (configurable through an option).
- deterministic: when we can pre-compute the boundaries of each page, it will perform the requests concurrently for maximum performance. This applies to OHLCV, Funding Rates, and Open Interest and also respects the maxPaginationCalls option.
- cursor-based: when the exchange provides a cursor inside the response, we extract the cursor and perform the subsequent request until the end of the data or reach the maximum number of pagination calls.

#### Pagination Params
+ paginate: (boolean) indicates that the user wants to paginate through different pages to get more data. Default is false.
+ paginationCalls: (integer) allows the user to control the maximum amount of requests to paginate the data. Due to the rate limits, this value should not be too high. Default is 10.
+ maxRetries: (integer) how many times should the pagination mechanism retry upon getting an error. Default is 3
+ paginationDirection: (string) Only applies to the dynamic pagination and it can be either forward (start the pagination from some time in the past and paginate forward) or backward (start from the most recent time and paginate backward). If forward is selected then a since parameter must also be provided. Default is backward.
+ maxEntriesPerRequest: (integer): The max amount of entries per request so that we can maximize the data retrieved per call. It varies from endpoint to endpoint and CCXT will populate this value for you, but you can override it if needed.

In [5]:
binance = ccxt.binance()
bybit = ccxt.bybit()

In [7]:
trades = await binance.fetch_trades("BTC/USDT", params = {"paginate": True}) # dynamic/time-based

ohlcv = await binance.fetch_ohlcv("BTC/USDT", params = {"paginate": True, "paginationCalls": 5}) # deterministic-pagination will perform 5 requests

trades = await binance.fetch_trades("BTC/USDT", since = 1664812416000, params = {"paginate": True, "paginationDirection": "forward"}) # dynamic/time-based pagination starting from 1664812416000

# ledger = await bybit.fetch_ledger(params = {"paginate": True}) # bybit returns a cursor so the pagination will be cursor-based

funding_rates = await binance.fetch_funding_rate_history("BTC/USDT:USDT", params = {"paginate": True, "maxEntriesPerRequest": 50}) # customizes the number of entries per request

In [8]:
print(trades)

[{'info': {'a': '1648357620', 'p': '19377.90000000', 'q': '0.00900000', 'f': '1919321831', 'l': '1919321831', 'T': '1664812416003', 'm': False, 'M': True}, 'timestamp': 1664812416003, 'datetime': '2022-10-03T15:53:36.003Z', 'symbol': 'BTC/USDT', 'id': '1648357620', 'order': None, 'type': None, 'side': 'buy', 'takerOrMaker': None, 'price': 19377.9, 'amount': 0.009, 'cost': 174.4011, 'fee': None, 'fees': []}, {'info': {'a': '1648357621', 'p': '19376.24000000', 'q': '0.00408000', 'f': '1919321832', 'l': '1919321832', 'T': '1664812416094', 'm': True, 'M': True}, 'timestamp': 1664812416094, 'datetime': '2022-10-03T15:53:36.094Z', 'symbol': 'BTC/USDT', 'id': '1648357621', 'order': None, 'type': None, 'side': 'sell', 'takerOrMaker': None, 'price': 19376.24, 'amount': 0.00408, 'cost': 79.0550592, 'fee': None, 'fees': []}, {'info': {'a': '1648357622', 'p': '19376.23000000', 'q': '0.06296000', 'f': '1919321833', 'l': '1919321833', 'T': '1664812416094', 'm': True, 'M': True}, 'timestamp': 1664812

In [9]:
print(ohlcv)

[[1719998760000, 60604.22, 60609.31, 60588.0, 60609.31, 29.9756], [1719998820000, 60609.31, 60637.49, 60609.3, 60637.49, 14.74364], [1719998880000, 60637.48, 60643.03, 60628.0, 60643.03, 21.5153], [1719998940000, 60643.03, 60665.42, 60630.5, 60630.51, 40.34403], [1719999000000, 60630.51, 60638.03, 60614.0, 60614.01, 17.9264], [1719999060000, 60614.01, 60614.01, 60605.88, 60610.84, 12.35555], [1719999120000, 60610.85, 60655.0, 60610.84, 60655.0, 12.13514], [1719999180000, 60654.99, 60663.64, 60654.99, 60662.01, 7.05246], [1719999240000, 60662.01, 60662.01, 60618.0, 60618.0, 7.15902], [1719999300000, 60618.01, 60644.0, 60618.0, 60644.0, 12.1842], [1719999360000, 60643.99, 60644.0, 60615.02, 60615.02, 10.08315], [1719999420000, 60615.03, 60624.36, 60614.01, 60624.0, 9.69455], [1719999480000, 60624.0, 60634.8, 60622.0, 60622.01, 12.99182], [1719999540000, 60622.0, 60634.0, 60614.01, 60622.26, 10.20845], [1719999600000, 60622.25, 60622.26, 60582.01, 60586.01, 14.96079], [1719999660000, 6058

In [10]:
print(funding_rates)

[{'info': {'symbol': 'BTCUSDT', 'fundingTime': '1705910400000', 'fundingRate': '0.00010000', 'markPrice': '41041.20808511'}, 'symbol': 'BTC/USDT:USDT', 'fundingRate': 0.0001, 'timestamp': 1705910400000, 'datetime': '2024-01-22T08:00:00.000Z'}, {'info': {'symbol': 'BTCUSDT', 'fundingTime': '1705939200000', 'fundingRate': '0.00010000', 'markPrice': '40767.10361702'}, 'symbol': 'BTC/USDT:USDT', 'fundingRate': 0.0001, 'timestamp': 1705939200000, 'datetime': '2024-01-22T16:00:00.000Z'}, {'info': {'symbol': 'BTCUSDT', 'fundingTime': '1705968000000', 'fundingRate': '0.00010000', 'markPrice': '39566.15381552'}, 'symbol': 'BTC/USDT:USDT', 'fundingRate': 0.0001, 'timestamp': 1705968000000, 'datetime': '2024-01-23T00:00:00.000Z'}, {'info': {'symbol': 'BTCUSDT', 'fundingTime': '1705996800000', 'fundingRate': '0.00010000', 'markPrice': '39777.14965957'}, 'symbol': 'BTC/USDT:USDT', 'fundingRate': 0.0001, 'timestamp': 1705996800000, 'datetime': '2024-01-23T08:00:00.000Z'}, {'info': {'symbol': 'BTCUSD

In [11]:
exchange = ccxt.binance()

#### Date-based Pagination
* This is the type of pagination currently used throughout the CCXT Unified API. The user supplies a since timestamp in milliseconds (!) and a number to limit results. To traverse the objects of interest page by page, the user runs the following (below is pseudocode, it may require overriding some exchange-specific params, depending on the exchange in question):

In [ ]:
if exchange.has['fetchOrders']:
    since = exchange.milliseconds() - 60 * 60 * 1000  # one hour ago
    while since < exchange.milliseconds():
        orders = await exchange.fetch_orders('BTC/USDT', since=since, limit=100)
        for order in orders:
            print(order)
        since = orders[-1]['timestamp'] + 1  # fetch the next page from the timestamp of the last order in the current page

In [ ]:
if exchange.has['fetchOrders']:
    since = exchange.milliseconds() - 60 * 60 * 1000  # one hour ago
    # alternatively, fetch from a certain starting datetime
    # since = exchange.parse8601('2018-01-01T00:00:00Z')
    all_orders = []
    while since < exchange.milliseconds():
        symbol = 'BTC/USDT'
        limit = 100
        # fetch the orders
        orders = await exchange.fetch_orders(symbol, since=since, limit=limit)
        all_orders.extend(orders)
        # update the since timestamp
        since = orders[-1]['timestamp'] + 1  # fetch the next page from the timestamp of the last order in the current page

In [ ]:
if exchange.has['fetchOrders']:
    since = exchange.milliseconds () - 86400000  # -1 day from now
    # alternatively, fetch from a certain starting datetime
    # since = exchange.parse8601('2018-01-01T00:00:00Z')
    all_orders = []
    while since < exchange.milliseconds ():
        symbol = 'BTC/USDT'  # change for your symbol
        limit = 20  # change for your limit
        orders = await exchange.fetch_orders(symbol, since, limit)
        if len(orders):
            since = orders[len(orders) - 1]['timestamp'] + 1
            all_orders += orders
        else:
            break


#### id-based Pagination 
* The user supplies a from_id of the object, from where the query should continue returning results, and a number to limit results. This is the default with some exchanges, however, this type is not unified (yet). To paginate objects based on their ids, the user would run the following:

In [ ]:
if exchange.has['fetchOrders']:
    from_id = 'abc123'    # all ids are strings
    all_orders = []
    while True:
        symbol = 'BTC/USDT'
        since = exchange.milliseconds() - 60 * 60 * 1000
        limit = 100
        params = {
            'from_id': from_id
        }
        orders = await exchange.fetch_orders(symbol, since, limit, params)
        if len(orders) == 0:
            break
        else:
            from_id = orders[len(orders) - 1]['id']
            all_orders += orders
        # if len(orders):
        #     from_id = orders[len(orders) - 1]['id']
        #     all_orders += orders
        # else:
        #     break

#### Pagenumber-based (Cursor) Pagination
* The user supplies a page number or an initial "cursor" value. The exchange returns a page of results and the next "cursor" value, to proceed from. Most of exchanges that implement this type of pagination will either return the next cursor within the response itself or will return the next cursor values within HTTP response headers.

In [ ]:
if exchange.has['fetchOrders']:
    cursor = 0   # exchange-specific type and value
    all_orders = []
    while True:
        symbol = 'BTC/USDT'
        since = exchange.milliseconds() - 60 * 60 * 1000
        limit = 100  # change for your limit
        params = {
            'cursor': cursor
        }
        orders = await exchange.fetch_orders(symbol, params=params)
        if len(orders) == 0:
            break
        else:
            cursor = exchange.last_response_headers['CB-AFTER']  # fetch the next cursor from the last order in the current page
            all_orders += orders
        # if len(orders):
        #     cursor = exchange.last_response_headers['CB-AFTER']
        #     all_orders += orders
        # else:
        #     break

### Public API

#### Order Book
* Exchanges expose information on open orders with bid (buy) and ask (sell) prices, volumes and other data. Usually there is a separate endpoint for querying current state (stack frame) of the order book for a particular market. An order book is also often called market depth. The order book information is used in the trading decision making process.

* To get data on order books, you can use

    + fetch_order_book () // for a single markets order books
    + fetch_order_books ( symbols ) // for multiple markets order books
    + fetch_order_books () // for the order books of all markets

In [ ]:
import time

delay = 2 # seconds
for symbol in exchange.markets:
    order_book = exchange.fetch_order_book(symbol)
    # print(f'Order book for {symbol}:')
    print(order_book)
    time.sleep(delay)

#### Order Book Structure

In [ ]:
order_book_structure = {
    'bids': [
        [ price, amount ], # [ float, float ]
        [ price, amount ],
        ...
    ],
    'asks': [
        [ price, amount ],
        [ price, amount ],
        ...
    ],
    'symbol': 'ETH/BTC', # a unified market symbol
    'timestamp': 1499280391811, # Unix Timestamp in milliseconds (seconds * 1000)
    'datetime': '2017-07-05T18:47:14.692Z', # ISO8601 datetime string with milliseconds
    'nonce': 1499280391811, # an increasing unique identifier of the orderbook snapshot
}